In [1]:
import time

import toml

from util.data_load import Data_load
from models.models import create_model
import torch
import torchvision
from torch.utils import data
import torchvision.transforms as transforms


class Bunch(dict):
    def __init__(self, *args, **kw):
        super().__init__(*args, **kw)
        self.__dict__ = self


def load_option(path):
    opt = toml.load(path)
    return Bunch(opt)

In [2]:
opt_path = 'options/train.toml'
opt = load_option(opt_path)

transform_mask = transforms.Compose(
    [transforms.Resize((opt.fineSize, opt.fineSize)),
     transforms.ToTensor(),
     ])
transform = transforms.Compose(
    [transforms.RandomHorizontalFlip(),
     transforms.Resize((opt.fineSize, opt.fineSize)),
     transforms.ToTensor(),
     transforms.Normalize(mean=[0.5] * 3, std=[0.5] * 3)])

dataset_train = Data_load(opt.dataroot, opt.maskroot,
                          transform, transform_mask)
iterator_train = (data.DataLoader(
    dataset_train, batch_size=opt.batchSize, shuffle=True))
print(len(dataset_train))
model = create_model(opt)

202599
csa_net
initialize network with normal
initialize network with normal
initialize network with normal
initialize network with normal
---------- Networks initialized -------------
UnetGeneratorCSA(
  (model): UnetSkipConnectionBlock_3(
    (model): Sequential(
      (0): Conv2d(6, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (1): UnetSkipConnectionBlock_3(
        (model): Sequential(
          (0): LeakyReLU(negative_slope=0.2, inplace=True)
          (1): Conv2d(64, 64, kernel_size=(4, 4), stride=(2, 2), padding=(3, 3), dilation=(2, 2))
          (2): InstanceNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=False)
          (3): LeakyReLU(negative_slope=0.2, inplace=True)
          (4): Conv2d(64, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
          (5): InstanceNorm2d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=False)
          (6): UnetSkipConnectionBlock_3(
            (model): Sequential(
              (0): 

In [3]:
total_steps = 0

iter_start_time = time.time()
for epoch in range(opt.epoch_count, opt.niter + opt.niter_decay + 1):
    epoch_start_time = time.time()
    epoch_iter = 0
#     image, mask, gt = [x.cuda() for x in next(iterator_train)]
    for image, mask in (iterator_train):
        image = image.cuda()
        mask = mask.cuda()
        mask = mask[0][0]
        mask = torch.unsqueeze(mask, 0)
        mask = torch.unsqueeze(mask, 1)
        mask = mask.byte()
        total_steps += opt.batchSize
        epoch_iter += opt.batchSize
        # it not only sets the input data with mask, but also sets the latent mask.
        model.set_input(image, mask)
        model.set_gt_latent()
        model.optimize_parameters()
        if total_steps % opt.display_freq == 0:
            real_A, real_B, fake_B = model.get_current_visuals()
            # real_A=input, real_B=ground truth fake_b=output
            pic = (torch.cat([real_A, real_B, fake_B], dim=0) + 1) / 2.0
            torchvision.utils.save_image(pic, '%s/Epoch_(%d)_(%dof%d).jpg' % (
                opt.save_dir, epoch, total_steps + 1, len(dataset_train)), nrow=2)
        if total_steps % 1 == 0:
            errors = model.get_current_errors()
            t = (time.time() - iter_start_time) / opt.batchSize
            print(errors)
    if epoch % opt.save_epoch_freq == 0:
        print('saving the model at the end of epoch %d, iters %d' %
              (epoch, total_steps))
        model.save(epoch)
    print('End of epoch %d / %d \t Time Taken: %d sec' %
          (epoch, opt.niter + opt.niter_decay, time.time() - epoch_start_time))
    model.update_learning_rate()

OrderedDict([('G_GAN', 11.576102256774902), ('G_L1', 112.62757873535156), ('D', 2.652731418609619), ('F', 2.3320555686950684)])
OrderedDict([('G_GAN', 11.333353042602539), ('G_L1', 71.17382049560547), ('D', 5.469654560089111), ('F', 1.987812876701355)])
OrderedDict([('G_GAN', 11.299707412719727), ('G_L1', 87.23036193847656), ('D', 12.112640380859375), ('F', 1.9138727188110352)])
OrderedDict([('G_GAN', 5.568836212158203), ('G_L1', 103.02356719970703), ('D', 6.654585838317871), ('F', 1.628221869468689)])
OrderedDict([('G_GAN', 5.857004165649414), ('G_L1', 84.03224182128906), ('D', 2.6696243286132812), ('F', 1.4683250188827515)])
OrderedDict([('G_GAN', 5.932779312133789), ('G_L1', 51.632850646972656), ('D', 1.9101513624191284), ('F', 1.3541662693023682)])
OrderedDict([('G_GAN', 6.553698539733887), ('G_L1', 89.87959289550781), ('D', 2.0671145915985107), ('F', 1.1484010219573975)])
OrderedDict([('G_GAN', 6.800159454345703), ('G_L1', 96.9000244140625), ('D', 1.5704576969146729), ('F', 0.9476

OrderedDict([('G_GAN', 6.025411605834961), ('G_L1', 42.53532028198242), ('D', 1.1096341609954834), ('F', 0.11049364507198334)])
OrderedDict([('G_GAN', 6.107933044433594), ('G_L1', 51.317169189453125), ('D', 2.093132972717285), ('F', 0.15694361925125122)])
OrderedDict([('G_GAN', 5.865786552429199), ('G_L1', 31.723690032958984), ('D', 1.3740713596343994), ('F', 0.12757784128189087)])
OrderedDict([('G_GAN', 5.913073539733887), ('G_L1', 42.58705139160156), ('D', 1.094065546989441), ('F', 0.1309809684753418)])
OrderedDict([('G_GAN', 5.864081382751465), ('G_L1', 34.13414764404297), ('D', 1.0604684352874756), ('F', 0.10217852890491486)])
OrderedDict([('G_GAN', 8.433610916137695), ('G_L1', 40.109214782714844), ('D', 1.0190730094909668), ('F', 0.08529497683048248)])
OrderedDict([('G_GAN', 5.985346794128418), ('G_L1', 32.24852752685547), ('D', 1.3609120845794678), ('F', 0.10208308696746826)])
OrderedDict([('G_GAN', 5.041051864624023), ('G_L1', 40.18273162841797), ('D', 1.2768176794052124), ('F',

OrderedDict([('G_GAN', 5.823681831359863), ('G_L1', 39.679019927978516), ('D', 0.8788102269172668), ('F', 0.05824627727270126)])
OrderedDict([('G_GAN', 5.930612564086914), ('G_L1', 38.208641052246094), ('D', 1.0981563329696655), ('F', 0.04205317422747612)])
OrderedDict([('G_GAN', 6.134062767028809), ('G_L1', 19.851898193359375), ('D', 1.1685118675231934), ('F', 0.05307348817586899)])
OrderedDict([('G_GAN', 5.88155460357666), ('G_L1', 29.18454360961914), ('D', 0.9495713114738464), ('F', 0.057296186685562134)])
OrderedDict([('G_GAN', 5.384252071380615), ('G_L1', 29.50365447998047), ('D', 0.966609001159668), ('F', 0.08257625997066498)])
OrderedDict([('G_GAN', 5.533442497253418), ('G_L1', 24.820079803466797), ('D', 0.9534869194030762), ('F', 0.08000672608613968)])
OrderedDict([('G_GAN', 5.7689127922058105), ('G_L1', 29.009777069091797), ('D', 0.8903239965438843), ('F', 0.05265020579099655)])
OrderedDict([('G_GAN', 5.488064765930176), ('G_L1', 32.81675720214844), ('D', 0.8616319894790649), 

OrderedDict([('G_GAN', 6.906949996948242), ('G_L1', 22.24031639099121), ('D', 0.36051976680755615), ('F', 0.12831857800483704)])
OrderedDict([('G_GAN', 7.2128095626831055), ('G_L1', 24.58320426940918), ('D', 0.5108320713043213), ('F', 0.08226028829813004)])
OrderedDict([('G_GAN', 6.18336820602417), ('G_L1', 24.55341148376465), ('D', 0.7508590221405029), ('F', 0.08728694915771484)])
OrderedDict([('G_GAN', 7.280542373657227), ('G_L1', 21.33382797241211), ('D', 0.19428789615631104), ('F', 0.06873038411140442)])
OrderedDict([('G_GAN', 6.21565055847168), ('G_L1', 26.82175636291504), ('D', 0.6681663990020752), ('F', 0.06304860860109329)])
OrderedDict([('G_GAN', 5.677934646606445), ('G_L1', 32.8543586730957), ('D', 0.9890730381011963), ('F', 0.0976502075791359)])
OrderedDict([('G_GAN', 6.860306262969971), ('G_L1', 36.90062713623047), ('D', 0.574675440788269), ('F', 0.06849180907011032)])
OrderedDict([('G_GAN', 6.938039302825928), ('G_L1', 22.91630744934082), ('D', 0.5559470653533936), ('F', 0

OrderedDict([('G_GAN', 6.375910758972168), ('G_L1', 29.284513473510742), ('D', 0.6152114868164062), ('F', 0.05867089703679085)])
OrderedDict([('G_GAN', 6.73492956161499), ('G_L1', 21.25379753112793), ('D', 0.4138319492340088), ('F', 0.05703898146748543)])
OrderedDict([('G_GAN', 7.413126468658447), ('G_L1', 25.733423233032227), ('D', 0.25865834951400757), ('F', 0.047732800245285034)])
OrderedDict([('G_GAN', 7.741140365600586), ('G_L1', 24.070873260498047), ('D', 0.5682751536369324), ('F', 0.027918953448534012)])
OrderedDict([('G_GAN', 7.460920333862305), ('G_L1', 35.251502990722656), ('D', 1.4113554954528809), ('F', 0.040586672723293304)])
OrderedDict([('G_GAN', 7.110231876373291), ('G_L1', 24.33102798461914), ('D', 0.5384217500686646), ('F', 0.05557361617684364)])
OrderedDict([('G_GAN', 6.782412528991699), ('G_L1', 18.620296478271484), ('D', 0.7393922805786133), ('F', 0.03496113419532776)])
OrderedDict([('G_GAN', 6.006009578704834), ('G_L1', 20.322031021118164), ('D', 0.938198924064636

...

OrderedDict([('G_GAN', 7.527895927429199), ('G_L1', 9.89528751373291), ('D', 0.14469866454601288), ('F', 0.002409223932772875)])
OrderedDict([('G_GAN', 7.103368759155273), ('G_L1', 9.264034271240234), ('D', 0.32209715247154236), ('F', 0.0013276718091219664)])
OrderedDict([('G_GAN', 8.798039436340332), ('G_L1', 11.582914352416992), ('D', 0.14245128631591797), ('F', 0.001543071586638689)])
OrderedDict([('G_GAN', 7.261410236358643), ('G_L1', 9.446537017822266), ('D', 0.19182200729846954), ('F', 0.004996501840651035)])
OrderedDict([('G_GAN', 5.812361717224121), ('G_L1', 6.014359951019287), ('D', 0.7409681081771851), ('F', 0.004821803420782089)])
OrderedDict([('G_GAN', 6.086869716644287), ('G_L1', 6.785878658294678), ('D', 0.7126055955886841), ('F', 0.0041786013171076775)])
OrderedDict([('G_GAN', 8.20927619934082), ('G_L1', 11.018104553222656), ('D', 0.09785875678062439), ('F', 0.005145100876688957)])
OrderedDict([('G_GAN', 6.205860137939453), ('G_L1', 7.624454975128174), ('D', 0.4934371113

OrderedDict([('G_GAN', 5.726378440856934), ('G_L1', 12.508405685424805), ('D', 0.9384639859199524), ('F', 0.003314430359750986)])
OrderedDict([('G_GAN', 7.158239364624023), ('G_L1', 12.313149452209473), ('D', 0.33984386920928955), ('F', 0.03659148886799812)])
OrderedDict([('G_GAN', 5.768719673156738), ('G_L1', 12.017363548278809), ('D', 0.9249472618103027), ('F', 0.005886483937501907)])
OrderedDict([('G_GAN', 7.410391330718994), ('G_L1', 11.155296325683594), ('D', 0.1493665874004364), ('F', 0.0025932365097105503)])
OrderedDict([('G_GAN', 7.527299880981445), ('G_L1', 14.252336502075195), ('D', 0.15461590886116028), ('F', 0.005213066935539246)])
OrderedDict([('G_GAN', 8.10601806640625), ('G_L1', 12.149168968200684), ('D', 0.11431217193603516), ('F', 0.0016710092313587666)])
OrderedDict([('G_GAN', 5.250723361968994), ('G_L1', 8.689529418945312), ('D', 1.5068936347961426), ('F', 0.0031162467785179615)])
OrderedDict([('G_GAN', 5.626349449157715), ('G_L1', 7.339849948883057), ('D', 2.2310748

OrderedDict([('G_GAN', 6.549999713897705), ('G_L1', 11.519129753112793), ('D', 0.47672051191329956), ('F', 0.0033510662615299225)])
OrderedDict([('G_GAN', 5.681034088134766), ('G_L1', 8.994680404663086), ('D', 1.1728508472442627), ('F', 0.002883972367271781)])
OrderedDict([('G_GAN', 6.890466213226318), ('G_L1', 7.8777289390563965), ('D', 0.8201073408126831), ('F', 0.007981046102941036)])
OrderedDict([('G_GAN', 5.718110084533691), ('G_L1', 7.002913951873779), ('D', 0.7600536346435547), ('F', 0.002827445510774851)])
OrderedDict([('G_GAN', 5.673897743225098), ('G_L1', 7.6182475090026855), ('D', 0.9051324129104614), ('F', 0.003363661002367735)])
OrderedDict([('G_GAN', 6.551794052124023), ('G_L1', 9.545190811157227), ('D', 0.3261148929595947), ('F', 0.004074567928910255)])
OrderedDict([('G_GAN', 6.403835296630859), ('G_L1', 6.7968010902404785), ('D', 0.4864286184310913), ('F', 0.0032169255428016186)])
OrderedDict([('G_GAN', 5.409266471862793), ('G_L1', 7.210616588592529), ('D', 1.3522269725

OrderedDict([('G_GAN', 5.004829406738281), ('G_L1', 8.350639343261719), ('D', 2.273960590362549), ('F', 0.002673287410289049)])
OrderedDict([('G_GAN', 7.236250400543213), ('G_L1', 6.487631797790527), ('D', 0.1871607005596161), ('F', 0.0051892767660319805)])
OrderedDict([('G_GAN', 6.352449417114258), ('G_L1', 9.431722640991211), ('D', 0.9884276986122131), ('F', 0.0014041236136108637)])
OrderedDict([('G_GAN', 6.337580680847168), ('G_L1', 8.84481143951416), ('D', 0.5350223779678345), ('F', 0.015075158327817917)])
OrderedDict([('G_GAN', 5.903568267822266), ('G_L1', 8.802960395812988), ('D', 0.9376223087310791), ('F', 0.008200457319617271)])
OrderedDict([('G_GAN', 7.514972686767578), ('G_L1', 5.723257064819336), ('D', 0.15037095546722412), ('F', 0.0040421150624752045)])
OrderedDict([('G_GAN', 6.825980186462402), ('G_L1', 12.553666114807129), ('D', 0.6089823246002197), ('F', 0.0027686713729053736)])
OrderedDict([('G_GAN', 7.668511390686035), ('G_L1', 6.966794967651367), ('D', 0.1908214986324

KeyboardInterrupt: 